<h3>Assignment 7 (Midsem)</h3>

In [491]:
import pandas as pd
import numpy as np
import plotly.express as px
from scipy.stats import kurtosis,skew
import statsmodels.api as sm
import matplotlib.pyplot as plt
# pd.set_option('display.max_rows', None)  # Show all rows
# pd.set_option('display.max_columns', None)  # Show all columns

In [492]:
df = pd.read_csv("e7-htr-currernt.csv")

In [493]:
current = list(df["HT R Phase Current"])
timestamp = list(df["Timestamp"])
days = []
for i in timestamp:
    k = i[:2]
    days.append(k)

In [494]:
df['Time'] = pd.to_datetime(df['Timestamp'], format='%d-%m-%Y %H:%M').dt.time
df['Day'] = pd.to_datetime(df['Timestamp'], format='%d-%m-%Y %H:%M').dt.day

In [495]:
day_hash = np.zeros(len(days))
day_hash[0] = int(1)
current_date = days[0]
index = int(1)
for k in range(0, len(days)):
    temp = days[k]
    if temp != current_date:
        index += int(1)
        current_date = temp
        day_hash[k] += int(index)
    else:
        day_hash[k] = int(index)

df["Day No."] = day_hash
df

Timestamp  HT R Phase Current      Time  Day  Day No.
0      23-12-2018 05:30                 0.0  05:30:00   23      1.0
1      23-12-2018 05:35                 0.0  05:35:00   23      1.0
2      23-12-2018 05:40                 0.0  05:40:00   23      1.0
3      23-12-2018 05:45                 0.0  05:45:00   23      1.0
4      23-12-2018 05:50                 0.0  05:50:00   23      1.0
...                 ...                 ...       ...  ...      ...
81721  04-10-2019 23:35                 0.0  23:35:00    4    285.0
81722  04-10-2019 23:40                 0.0  23:40:00    4    285.0
81723  04-10-2019 23:45                 0.0  23:45:00    4    285.0
81724  04-10-2019 23:50                 0.0  23:50:00    4    285.0
81725  04-10-2019 23:55                 0.0  23:55:00    4    285.0

[81726 rows x 5 columns]

In [496]:
overall_avg = np.mean(df["HT R Phase Current"])
# print(overall_avg)
Mean, Error, Std_dev = [], [], []
Daily_readings = []
for i in range(1, 286):
    __ = df.loc[df["Day No."] == i]
    readings = __["HT R Phase Current"]
    Daily_readings.append(readings)
    mean = np.mean(readings)
    Mean.append(mean)
    error = overall_avg - mean
    Error.append(error)
    std_dev = np.std(readings)
    Std_dev.append(std_dev)
    # median = np.median(readings)
    # Median.append(median)
    # print(f"Day {i}: Overall Mean = {overall_avg}, Mean = {mean}, Median = {median}, Error = {error}, Standard Deviation = {std_dev}.")

In [497]:
Days = np.arange(1,day_hash[len(day_hash) - 1] + 1)
labels = ['Day', 'Mean', 'Error', 'Standard Deviation']
data = {'Day':Days, 'Mean': Mean, 'Error': Error, 'Standard Deviation': Std_dev}
Daily_data = pd.DataFrame(data)
# Daily_data.sort_values(by='Mean')
Daily_data

Day       Mean      Error  Standard Deviation
0      1.0  18.279009  -1.366242           25.055922
1      2.0  10.687778   6.224990           19.593635
2      3.0  21.503611  -4.590844           27.659036
3      4.0  17.451354  -0.538587           24.114771
4      5.0  15.338750   1.574017           22.766003
..     ...        ...        ...                 ...
280  281.0   0.520937  16.391830            2.158942
281  282.0  17.338472  -0.425705           27.436700
282  283.0  22.156528  -5.243760           31.298513
283  284.0  20.435000  -3.522233           29.790071
284  285.0   0.000000  16.912767            0.000000

[285 rows x 4 columns]

In [498]:
px.line(df,x=df['Timestamp'], y=['HT R Phase Current'], animation_frame=df['Day No.']).update_yaxes(range=[0,100])

In [499]:
def data_points_in_range(day, tolerance):
    upper_lim = Mean[day-1]+tolerance*Std_dev[day-1]
    lower_lim = Mean[day-1]-tolerance*Std_dev[day-1]
    req_data1 = df['HT R Phase Current'][df['Day No.']==day]
    normal_data = (req_data1[(df['HT R Phase Current']>lower_lim) & (df['HT R Phase Current']<upper_lim)]).tolist()
    return len(normal_data)/len(req_data1)

normal_points_count = [data_points_in_range(day, tolerance=1.1)*100 for day in range(1, int(day_hash[len(day_hash) - 1]) + 1)]
Daily_data['Normal points (%)'] = normal_points_count

def unwanted_points(day, threshold=1):
    req_data2 = df['HT R Phase Current'][df['Day No.'] == day]
    readings_less_than_threshold = (req_data2 < threshold).sum()  
    return (readings_less_than_threshold / len(req_data2)) * 100 

unwanted = [unwanted_points(day) for day in range(1, int(day_hash[len(day_hash) - 1]) + 1)]
Daily_data['Unwanted (%)'] = unwanted

def std_dev_bandwidth(day, threshold):
    req_data = df['HT R Phase Current'][df['HT R Phase Current'] >= threshold][df['Day No.']==day]
    Std_dev_band = np.std(req_data)
    return Std_dev_band
std_dev_band_data = [std_dev_bandwidth(day, threshold=45) for day in range(1, int(day_hash[len(day_hash) - 1]) + 1)]
Daily_data['Band Standard Deviation'] = std_dev_band_data
Daily_data

Day       Mean      Error  Standard Deviation  Normal points (%)  \
0      1.0  18.279009  -1.366242           25.055922          77.027027   
1      2.0  10.687778   6.224990           19.593635          84.722222   
2      3.0  21.503611  -4.590844           27.659036          73.263889   
3      4.0  17.451354  -0.538587           24.114771          76.388889   
4      5.0  15.338750   1.574017           22.766003          79.513889   
..     ...        ...        ...                 ...                ...   
280  281.0   0.520937  16.391830            2.158942          94.444444   
281  282.0  17.338472  -0.425705           27.436700          82.291667   
282  283.0  22.156528  -5.243760           31.298513          78.125000   
283  284.0  20.435000  -3.522233           29.790071          79.513889   
284  285.0   0.000000  16.912767            0.000000           0.000000   

     Unwanted (%)  Band Standard Deviation  
0       54.504505                 5.941775  
1       68.750000                 4.007286  
2       54.513889                 6.169857  
3       56.944444                 4.700600  
4       56.250000                 5.098244  
..            ...                      ...  
280     93.402778                      NaN  
281     51.736111                10.929561  
282     52.777778                11.695472  
283     55.902778                11.396924  
284    100.000000                      NaN  

[285 rows x 7 columns]

In [500]:
Daily_data.to_csv('Daily_data.csv')

In [501]:
Good_days = Daily_data['Day'][Daily_data['Normal points (%)']>50][Daily_data['Unwanted (%)']<60][Daily_data['Mean']>21][(Daily_data['Standard Deviation']<33)][Daily_data['Band Standard Deviation']<9]
good_day_disp = np.array(Good_days)
print(good_day_disp)
print(f"Number of good days are {len(Good_days)}.")

[  3.   7.   8.   9.  10.  37.  41.  42.  44.  45.  48.  49.  52.  58.
  79.  94.  95.  96.  97. 100. 101. 102. 104. 105. 107. 108. 111. 112.
 122. 123. 124. 125. 126. 127. 128. 129. 131. 135. 138. 139. 141. 145.
 146. 147. 148. 149. 150. 151. 152. 153. 154. 155. 159. 163. 164. 168.
 169. 207. 262.]
Number of good days are 59.


In [502]:
Good_days_data = df[df['Day No.'].isin(Good_days)]
Good_days_data

Timestamp  HT R Phase Current      Time  Day  Day No.
510    25-12-2018 00:00                0.10  00:00:00   25      3.0
511    25-12-2018 00:05                0.10  00:05:00   25      3.0
512    25-12-2018 00:10                0.10  00:10:00   25      3.0
513    25-12-2018 00:15                0.10  00:15:00   25      3.0
514    25-12-2018 00:20                0.10  00:20:00   25      3.0
...                 ...                 ...       ...  ...      ...
75097  11-09-2019 23:35                0.11  23:35:00   11    262.0
75098  11-09-2019 23:40                0.11  23:40:00   11    262.0
75099  11-09-2019 23:45                0.11  23:45:00   11    262.0
75100  11-09-2019 23:50                0.11  23:50:00   11    262.0
75101  11-09-2019 23:55                0.11  23:55:00   11    262.0

[16992 rows x 5 columns]

In [503]:
px.line(Good_days_data,x=Good_days_data['Timestamp'], y=['HT R Phase Current'], animation_frame=Good_days_data['Day No.']).update_yaxes(range=[0,100])

In [504]:
data = Good_days_data[Good_days_data['Day No.'].isin(Good_days)]
Smoothened_data = data['HT R Phase Current'].ewm(span=25, adjust=False).mean()
Good_days_data['Smoothened Current Values'] = Smoothened_data
Good_days_data

/tmp/ipykernel_10420/1356908457.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



Timestamp  HT R Phase Current      Time  Day  Day No.  \
510    25-12-2018 00:00                0.10  00:00:00   25      3.0   
511    25-12-2018 00:05                0.10  00:05:00   25      3.0   
512    25-12-2018 00:10                0.10  00:10:00   25      3.0   
513    25-12-2018 00:15                0.10  00:15:00   25      3.0   
514    25-12-2018 00:20                0.10  00:20:00   25      3.0   
...                 ...                 ...       ...  ...      ...   
75097  11-09-2019 23:35                0.11  23:35:00   11    262.0   
75098  11-09-2019 23:40                0.11  23:40:00   11    262.0   
75099  11-09-2019 23:45                0.11  23:45:00   11    262.0   
75100  11-09-2019 23:50                0.11  23:50:00   11    262.0   
75101  11-09-2019 23:55                0.11  23:55:00   11    262.0   

       Smoothened Current Values  
510                     0.100000  
511                     0.100000  
512                     0.100000  
513                     0.100000  
514                     0.100000  
...                          ...  
75097                   0.176215  
75098                   0.171121  
75099                   0.166420  
75100                   0.162080  
75101                   0.158074  

[16992 rows x 6 columns]

In [505]:
px.line(Good_days_data,x=Good_days_data['Timestamp'], y=['Smoothened Current Values'], animation_frame=Good_days_data['Day No.']).update_yaxes(range=[0,100])

In [506]:
import random
training_days = Good_days_data['Day No.'].sample(n=int(0.8*len(Good_days_data)), random_state=random.randint(0,284))
testing_days = Good_days_data['Day No.'].drop(index=training_days.index)
training_days

36302    128.0
44255    155.0
36782    129.0
2101       8.0
38273    135.0
         ...  
30284    107.0
28534    101.0
29798    105.0
30201    107.0
2125       8.0
Name: Day No., Length: 13593, dtype: float64

In [507]:
Training_data = Good_days_data[Good_days_data['Day No.'].isin(training_days)]
Training_data['Time'] = Training_data['Time'].apply(lambda x: x.hour + x.minute/60)
Training_data['Time2'] = Training_data['Time']**2
Training_data['Time3'] = Training_data['Time']**3
Training_data['Time4'] = Training_data['Time']**4
Training_data['Time5'] = Training_data['Time']**5
Training_data['Time6'] = Training_data['Time']**6
Training_data['Time7'] = Training_data['Time']**7
Training_data['Day2'] = Training_data['Day']**2
Training_data

Timestamp  HT R Phase Current       Time  Day  Day No.  \
510    25-12-2018 00:00                0.10   0.000000   25      3.0   
511    25-12-2018 00:05                0.10   0.083333   25      3.0   
512    25-12-2018 00:10                0.10   0.166667   25      3.0   
513    25-12-2018 00:15                0.10   0.250000   25      3.0   
514    25-12-2018 00:20                0.10   0.333333   25      3.0   
...                 ...                 ...        ...  ...      ...   
75097  11-09-2019 23:35                0.11  23.583333   11    262.0   
75098  11-09-2019 23:40                0.11  23.666667   11    262.0   
75099  11-09-2019 23:45                0.11  23.750000   11    262.0   
75100  11-09-2019 23:50                0.11  23.833333   11    262.0   
75101  11-09-2019 23:55                0.11  23.916667   11    262.0   

       Smoothened Current Values       Time2         Time3          Time4  \
510                     0.100000    0.000000      0.000000       0.000000   
511                     0.100000    0.006944      0.000579       0.000048   
512                     0.100000    0.027778      0.004630       0.000772   
513                     0.100000    0.062500      0.015625       0.003906   
514                     0.100000    0.111111      0.037037       0.012346   
...                          ...         ...           ...            ...   
75097                   0.176215  556.173611  13116.427662  309329.085696   
75098                   0.171121  560.111111  13255.962963  313724.456790   
75099                   0.166420  564.062500  13396.484375  318166.503906   
75100                   0.162080  568.027778  13537.995370  322655.556327   
75101                   0.158074  572.006944  13680.499421  327191.944493   

              Time5         Time6         Time7  Day2  
510    0.000000e+00  0.000000e+00  0.000000e+00   625  
511    4.018776e-06  3.348980e-07  2.790816e-08   625  
512    1.286008e-04  2.143347e-05  3.572245e-06   625  
513    9.765625e-04  2.441406e-04  6.103516e-05   625  
514    4.115226e-03  1.371742e-03  4.572474e-04   625  
...             ...           ...           ...   ...  
75097  7.295011e+06  1.720407e+08  4.057293e+09   121  
75098  7.424812e+06  1.757206e+08  4.158720e+09   121  
75099  7.556454e+06  1.794658e+08  4.262313e+09   121  
75100  7.689957e+06  1.832773e+08  4.368109e+09   121  
75101  7.825341e+06  1.871561e+08  4.476149e+09   121  

[16992 rows x 13 columns]

In [ ]:
import statsmodels.api as sm
#filtered_df['Time'] = pd.to_datetime(filtered_df['Time'])
drop_columns = ['Timestamp', 'HT R Phase Current', 'Date', 'Day Index', 'EMA Current']
X_train = Training_data.drop(columns=drop_columns)
X_train = sm.add_constant(X_train)
y_train = Training_data['EMA Current']
model = sm.OLS(y_train, X_train).fit()
print(model.summary())

In [ ]:
testing_df = filtered_df[filtered_df['Day Index'].isin(testing_days)]
testing_df['Time'] = testing_df['Time'].apply(lambda x: x.hour + x.minute/60)
testing_df['Time2'] = testing_df['Time']**2
testing_df['Time3'] = testing_df['Time']**3
testing_df['Time4'] = testing_df['Time']**4
testing_df['Time5'] = testing_df['Time']**5
testing_df['Time6'] = testing_df['Time']**6
testing_df['Time7'] = testing_df['Time']**7
testing_df['Day2'] = testing_df['Day']**2
testing_df

In [ ]:
drop_columns = ['Timestamp', 'HT R Phase Current', 'Date', 'Day Index', 'EMA Current']
X_test = Training_data.drop(columns=drop_columns)
X_test = sm.add_constant(X_test)
y_test = Training_data['EMA Current']
y_pred_test = model.predict(X_test)

In [ ]:
X_test

In [ ]:
import sklearn.metrics as metrics
y = training_df['HT R Phase Current']
print(metrics.r2_score(y, y_pred_test))
print(metrics.r2_score(y_test, y_pred_test))

In [ ]:
testing_df['Pred Current'] = np.array(y_pred_test[-len(testing_df):]).reshape(-1, 1)
px.line(testing_df, x='Timestamp', y=['HT R Phase Current', 'Pred Current'], animation_frame='Day Index').update_yaxes(range=[0,100])

In [ ]:
df['Time'] = pd.to_datetime(df['Time'], format='%H:%M:%S').dt.time
df['Time'] = df['Time'].apply(lambda x: x.hour + x.minute/60)
df

In [ ]:
df['Time2'] = df['Time']**2
df['Time3'] = df['Time']**3
df['Time4'] = df['Time']**4
df['Time5'] = df['Time']**5
df['Time6'] = df['Time']**6
df['Time7'] = df['Time']**7
df['Day2'] = df['Day']**2
df

In [ ]:
drop_columns = ['Timestamp', 'HT R Phase Current', 'Date', 'Day Index']
X_data = df.drop(columns=drop_columns)
X_data = sm.add_constant(X_data)
y_data = df['HT R Phase Current']
y_pred = model.predict(X_data)
print(metrics.r2_score(y_data, y_pred))
df['Pred Current'] = y_pred

In [ ]:
px.line(df, x='Timestamp', y=['HT R Phase Current', 'Pred Current'], animation_frame='Day Index')